# **Bitcoin price forecasting - GeneralizedLinearRegression**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



# Dependencies, Libraries and Tools

In [1]:
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "GeneralizedLinearRegression"
SLOW_OPERATION = False

In [2]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [3]:
#Install some useful dependencies
import requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from itertools import cycle

import plotly.express as px

import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import gc

import pandas as pd
import numpy as np
import json

import matplotlib.pyplot as plt
import seaborn as sns

In [4]:
# Install Spark and related dependencies
!pip install pyspark

import pyspark
from pyspark.sql import *
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark import SparkContext, SparkConf

from pyspark.ml.regression import LinearRegression, RandomForestRegressor, GBTRegressor
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation
from pyspark.ml import Pipeline

# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 2.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=1ce3d1bd13432085283f6f8c1e70b40a96cda1d9e5b503b2e706d4f7314bf7fc
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


# Link to Google Drive

In [5]:
# Define GDrive paths
GDRIVE_DIR = "/content/drive"

GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"

GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_eng"

GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"

GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG


In [6]:
# Point Colaboratory to our Google Drive
from google.colab import drive

drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [7]:
# Load datasets into pyspark dataframe objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

# Import my utilities

In [33]:
import sys
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"
sys.path.append(GDRIVE_UTILITIES_DIR)

import shutil
shutil.rmtree(GDRIVE_UTILITIES_DIR + '/__pycache__')

import utilities

import importlib
importlib.reload(utilities)

<module 'utilities' from '/content/drive/MyDrive/BDC/project/utilities/utilities.py'>

# Loading features

In [9]:
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"

GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_CORR_FEATURES_NAME = "corr_features"

GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_CORR_FEATURES_NAME_EXT = "/" + GDRIVE_CORR_FEATURES_NAME + ".json"

GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_CORR_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_CORR_FEATURES_NAME_EXT

In [10]:
# Set the target variable
TARGET_VAL = 'next-market-price'

# Set the features label
FEATURES_LABEL = "features"

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_CORR_FEATURES, "r") as f:
    corr_features = json.load(f)
print(corr_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins', 'sma-50-days', 'sma-20-days', 'difficulty', 'hash-rate', 'n-unique-addresses']


# Evaluation of a simple model

In [13]:
# Get default params
params = utilities.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [25],
 'regParam': [0],
 'family': ['gaussian'],
 'link': ['identity']}

In [14]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_all

Model    Type      Features  \
0  GeneralizedLinearRegression  simple  all_features   

                    Parameters         RMSE      MAPE          MAE  \
0  [25, 0, gaussian, identity]  1393.450931  0.050496  1214.427704   

       Variance        R2  Adjusted_R2      Time  
0  1.904857e+08  0.990445     0.990443  6.544161

In [15]:
utilities.show_results(simple_pred_all, MODEL_NAME)

In [16]:
# Valid performances with the corr matrix features
simple_res_corr, simple_pred_corr = utilities.evaluate_simple_model(df, corr_features, params, GDRIVE_CORR_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_corr

Model    Type       Features  \
0  GeneralizedLinearRegression  simple  corr_features   

                    Parameters         RMSE      MAPE          MAE  \
0  [25, 0, gaussian, identity]  1431.623438  0.050486  1210.965778   

       Variance        R2  Adjusted_R2      Time  
0  1.906849e+08  0.989914     0.989912  1.765945

In [17]:
utilities.show_results(simple_pred_corr, MODEL_NAME)

# Hyperparameter tuning

In [18]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [19]:
# Get simple params
params = utilities.get_simple_model_params(MODEL_NAME)
params

{'maxIter': [5, 10, 50, 80],
 'regParam': [0, 0.1, 0.2],
 'family': ['gaussian', 'gamma'],
 'link': ['identity', 'inverse']}

In [20]:
hyp_res_all = utilities.autoTuning(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res_all

Model        Type      Features  Proportion  \
0  GeneralizedLinearRegression  autotuning  all_features         0.9   

                     Parameters        RMSE      MAPE         MAE  \
0  [5, 0.2, gaussian, identity]  509.935916  0.019008  385.361908   

       Variance       R2  Adjusted_R2      Time  
0  6.200767e+06  0.95638     0.956363  0.199503

In [21]:
hyp_res_corr = utilities.autoTuning(df, corr_features, params, GDRIVE_CORR_FEATURES_NAME, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res_corr

Model        Type       Features  Proportion  \
0  GeneralizedLinearRegression  autotuning  corr_features         0.9   

                   Parameters        RMSE      MAPE         MAE      Variance  \
0  [10, 0.2, gamma, identity]  763.763361  0.030618  616.529791  6.569252e+06   

         R2  Adjusted_R2      Time  
0  0.902148     0.902109  1.368499

# Cross validation

In [35]:
# Get tuned params
params = utilities.get_tuned_model_params(MODEL_NAME)
params

{'maxIter': [5],
 'regParam': [0.2],
 'family': ['gaussian'],
 'link': ['identity']}

In [36]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [37]:
mul_cv_res_all, trained_models_mul_cv = utilities.tsCrossValidation(df, all_features, params, mul_cv, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res_all

Model   Type      Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  mulTs  all_features       1   (21030, 21029)   
1  GeneralizedLinearRegression  mulTs  all_features       2   (42059, 21029)   
2  GeneralizedLinearRegression  mulTs  all_features       3   (63088, 21029)   
3  GeneralizedLinearRegression  mulTs  all_features       4   (84117, 21029)   
4  GeneralizedLinearRegression  mulTs  all_features       5  (105146, 21029)   

                     Parameters         RMSE      MAPE          MAE  \
0  [5, 0.2, gaussian, identity]   585.952978  0.049382   381.110521   
1  [5, 0.2, gaussian, identity]   414.428978  0.055425   331.634515   
2  [5, 0.2, gaussian, identity]   977.387574  0.107026   920.183015   
3  [5, 0.2, gaussian, identity]  2728.676711  0.052540  2311.312180   
4  [5, 0.2, gaussian, identity]   662.152092  0.019769   495.030188   

       Variance        R2  Adjusted_R2      Time  
0  2.062719e+07  0.981072     0.981068  1.822234  
1  4.568913e+06  0.964395     0.964386  1.124074  
2  2.721156e+06  0.576896     0.576796  0.850482  
3  2.331115e+08  0.963545     0.963536  1.040620  
4  9.316555e+07  0.995359     0.995358  1.204186

In [38]:
mul_cv_res_corr, trained_models_mul_cv = utilities.tsCrossValidation(df, corr_features, params, mul_cv, GDRIVE_CORR_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res_corr

Model   Type       Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  mulTs  corr_features       1   (21030, 21029)   
1  GeneralizedLinearRegression  mulTs  corr_features       2   (42059, 21029)   
2  GeneralizedLinearRegression  mulTs  corr_features       3   (63088, 21029)   
3  GeneralizedLinearRegression  mulTs  corr_features       4   (84117, 21029)   
4  GeneralizedLinearRegression  mulTs  corr_features       5  (105146, 21029)   

                     Parameters         RMSE      MAPE          MAE  \
0  [5, 0.2, gaussian, identity]   512.749286  0.042910   318.292584   
1  [5, 0.2, gaussian, identity]   961.399309  0.157606   883.127370   
2  [5, 0.2, gaussian, identity]  1138.748703  0.124476  1077.236832   
3  [5, 0.2, gaussian, identity]  2745.491598  0.052745  2313.448441   
4  [5, 0.2, gaussian, identity]   757.876624  0.023895   584.832145   

       Variance        R2  Adjusted_R2      Time  
0  1.915163e+07  0.985506     0.985503  1.170069  
1  5.515163e+06  0.808388     0.808342  0.714751  
2  3.115688e+06  0.425660     0.425523  0.875900  
3  2.328796e+08  0.963094     0.963085  0.960150  
4  9.173134e+07  0.993920     0.993918  0.830842

In [39]:
blk_cv_res_all, trained_models_mul_cv = utilities.tsCrossValidation(df, all_features, params, blk_cv, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res_all

Model   Type      Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  blkTs  all_features       1    (10093, 2524)   
1  GeneralizedLinearRegression  blkTs  all_features       2    (10093, 2524)   
2  GeneralizedLinearRegression  blkTs  all_features       3    (10093, 2524)   
3  GeneralizedLinearRegression  blkTs  all_features       4    (10093, 2524)   
4  GeneralizedLinearRegression  blkTs  all_features       5    (10093, 2524)   
5  GeneralizedLinearRegression  blkTs  all_features       6    (10093, 2524)   
6  GeneralizedLinearRegression  blkTs  all_features       7    (10093, 2524)   
7  GeneralizedLinearRegression  blkTs  all_features       8    (10093, 2524)   
8  GeneralizedLinearRegression  blkTs  all_features       9    (10093, 2524)   
9  GeneralizedLinearRegression  blkTs  all_features      10    (10093, 2524)   

                     Parameters         RMSE      MAPE          MAE  \
0  [5, 0.2, gaussian, identity]     6.635890  0.008782     5.137243   
1  [5, 0.2, gaussian, identity]    56.194795  0.019784    38.600171   
2  [5, 0.2, gaussian, identity]   437.981820  0.033916   361.185818   
3  [5, 0.2, gaussian, identity]   212.924749  0.026652   169.754051   
4  [5, 0.2, gaussian, identity]   560.671759  0.045428   481.514894   
5  [5, 0.2, gaussian, identity]   421.908744  0.049825   345.444190   
6  [5, 0.2, gaussian, identity]   699.421453  0.019764   491.550582   
7  [5, 0.2, gaussian, identity]  1168.830285  0.019256   871.822245   
8  [5, 0.2, gaussian, identity]  1290.982160  0.039366  1065.027842   
9  [5, 0.2, gaussian, identity]   337.243774  0.010930   251.268362   

       Variance        R2  Adjusted_R2      Time  
0  3.859486e+02  0.908651     0.908470  0.917401  
1  2.569617e+05  0.986878     0.986852  1.415939  
2  4.421538e+06  0.960673     0.960595  0.971263  
3  6.224609e+04 -0.054262    -0.056355  0.786113  
4  1.086291e+06  0.627813     0.627074  0.956231  
5  7.895515e+05  0.763140     0.762670  0.647298  
6  4.859989e+07  0.989961     0.989941  0.559277  
7  4.650694e+06  0.797811     0.797410  0.621616  
8  2.698526e+07  0.927847     0.927704  1.204265  
9  1.193589e+06  0.881992     0.881757  1.186684

In [40]:
blk_cv_res_corr, trained_models_mul_cv = utilities.tsCrossValidation(df, corr_features, params, blk_cv, GDRIVE_CORR_FEATURES_NAME,MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res_corr

Model   Type       Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  blkTs  corr_features       1    (10093, 2524)   
1  GeneralizedLinearRegression  blkTs  corr_features       2    (10093, 2524)   
2  GeneralizedLinearRegression  blkTs  corr_features       3    (10093, 2524)   
3  GeneralizedLinearRegression  blkTs  corr_features       4    (10093, 2524)   
4  GeneralizedLinearRegression  blkTs  corr_features       5    (10093, 2524)   
5  GeneralizedLinearRegression  blkTs  corr_features       6    (10093, 2524)   
6  GeneralizedLinearRegression  blkTs  corr_features       7    (10093, 2524)   
7  GeneralizedLinearRegression  blkTs  corr_features       8    (10093, 2524)   
8  GeneralizedLinearRegression  blkTs  corr_features       9    (10093, 2524)   
9  GeneralizedLinearRegression  blkTs  corr_features      10    (10093, 2524)   

                     Parameters         RMSE      MAPE          MAE  \
0  [5, 0.2, gaussian, identity]    14.675936  0.023064    13.613230   
1  [5, 0.2, gaussian, identity]    59.385335  0.020528    41.241681   
2  [5, 0.2, gaussian, identity]   753.013404  0.063287   671.730247   
3  [5, 0.2, gaussian, identity]   188.949397  0.024975   159.492972   
4  [5, 0.2, gaussian, identity]   659.800586  0.052934   558.505219   
5  [5, 0.2, gaussian, identity]   602.111579  0.072920   505.718216   
6  [5, 0.2, gaussian, identity]   922.253719  0.023918   621.901977   
7  [5, 0.2, gaussian, identity]  1700.716570  0.027237  1221.069912   
8  [5, 0.2, gaussian, identity]  2096.013015  0.064906  1705.319908   
9  [5, 0.2, gaussian, identity]   516.962382  0.017063   390.863237   

       Variance        R2  Adjusted_R2      Time  
0  5.798346e+02  0.553198     0.552311  0.614105  
1  2.278468e+05  0.985345     0.985316  0.641682  
2  5.426465e+06  0.883752     0.883521  0.651506  
3  5.843944e+04  0.169792     0.168143  0.570363  
4  1.172190e+06  0.484571     0.483547  0.598163  
5  9.791889e+05  0.517599     0.516641  0.497010  
6  4.420709e+07  0.982546     0.982511  0.639338  
7  4.742285e+06  0.571927     0.571077  0.834141  
8  3.491492e+07  0.809804     0.809427  0.695749  
9  1.207027e+06  0.722704     0.722154  0.466957

# Comparison table

In [41]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_corr, hyp_res_all, hyp_res_corr, mul_cv_res_all, mul_cv_res_corr, blk_cv_res_all, blk_cv_res_corr]

In [42]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model        Type       Features  \
0  GeneralizedLinearRegression      simple   all_features   
0  GeneralizedLinearRegression      simple  corr_features   
0  GeneralizedLinearRegression  autotuning   all_features   
0  GeneralizedLinearRegression  autotuning  corr_features   
0  GeneralizedLinearRegression       mulTs   all_features   
0  GeneralizedLinearRegression       mulTs  corr_features   
0  GeneralizedLinearRegression       blkTs   all_features   
0  GeneralizedLinearRegression       blkTs  corr_features   

                     Parameters         RMSE      MAPE          MAE  \
0   [25, 0, gaussian, identity]  1393.450931  0.050496  1214.427704   
0   [25, 0, gaussian, identity]  1431.623438  0.050486  1210.965778   
0  [5, 0.2, gaussian, identity]   509.935916  0.019008   385.361908   
0    [10, 0.2, gamma, identity]   763.763361  0.030618   616.529791   
0  [5, 0.2, gaussian, identity]  1073.719667  0.056829   887.854084   
0  [5, 0.2, gaussian, identity]  1223.253104  0.080326  1035.387475   
0  [5, 0.2, gaussian, identity]   519.279543  0.027370   408.130540   
0  [5, 0.2, gaussian, identity]   751.388192  0.039083   588.945660   

       Variance        R2  Adjusted_R2      Time  
0  1.904857e+08  0.990445     0.990443  6.544161  
0  1.906849e+08  0.989914     0.989912  1.765945  
0  6.200767e+06  0.956380     0.956363  0.199503  
0  6.569252e+06  0.902148     0.902109  1.368499  
0  7.083886e+07  0.896253     0.896229  1.208319  
0  7.047868e+07  0.835313     0.835274  0.910343  
0  8.804641e+06  0.779051     0.778612  0.926609  
0  9.293603e+06  0.668124     0.667465  0.620901

# Training the final model

In [43]:
model = utilities.train_final_model(df, corr_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [44]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [45]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)